Convolutional Dictionary Learning
=================================

This example demonstrates the use of [dictlrn.cbpdndl.ConvBPDNDictLearn](http://sporco.rtfd.org/en/latest/modules/sporco.dictlrn.cbpdndl.html#sporco.dictlrn.cbpdndl.ConvBPDNDictLearn) for learning a convolutional dictionary from a set of training images. The dictionary learning algorithm is based on the ADMM consensus dictionary update [[1]](http://sporco.rtfd.org/en/latest/zreferences.html#sorel-2016-fast) [[17]](http://sporco.rtfd.org/en/latest/zreferences.html#garcia-2017-convolutional).

In [1]:
from __future__ import print_function
from builtins import input
from builtins import range

import pyfftw   # See https://github.com/pyFFTW/pyFFTW/issues/40
import numpy as np

from sporco.dictlrn import cbpdndl
from sporco import util
from sporco import plot
plot.config_notebook_plotting()

Load training images.

In [2]:
exim = util.ExampleImages(scaled=True, zoom=0.25, gray=True)
S1 = exim.image('barbara.png', idxexp=np.s_[10:522, 100:612])
S2 = exim.image('kodim23.png', idxexp=np.s_[:, 60:572])
S3 = exim.image('monarch.png', idxexp=np.s_[:, 160:672])
S4 = exim.image('sail.png', idxexp=np.s_[:, 210:722])
S5 = exim.image('tulips.png', idxexp=np.s_[:, 30:542])
S = np.dstack((S1, S2, S3, S4, S5))

Highpass filter training images.

In [3]:
npd = 16
fltlmbd = 5
sl, sh = util.tikhonov_filter(S, fltlmbd, npd)

Construct initial dictionary.

In [4]:
np.random.seed(12345)
D0 = np.random.randn(8, 8, 64)

Set regularization parameter and options for dictionary learning solver.

In [5]:
lmbda = 0.2
opt = cbpdndl.ConvBPDNDictLearn.Options({'Verbose': True, 'MaxMainIter': 200,
                            'CBPDN': {'rho': 50.0*lmbda + 0.5},
                            'CCMOD': {'rho': 10.0, 'ZeroMean': True}},
                            dmethod='cns')

Create solver object and solve.

In [6]:
d = cbpdndl.ConvBPDNDictLearn(D0, sh, lmbda, opt, dmethod='cns')
D1 = d.solve()
print("ConvBPDNDictLearn solve time: %.2fs" % d.timer.elapsed('solve'))

Itn   Fnc       DFid      ℓ1        Cnstr     r_X       s_X       ρ_X       r_D       s_D       ρ_D     
--------------------------------------------------------------------------------------------------------


   0  1.03e+03  1.21e+01  5.10e+03  6.31e-07  1.00e+00  4.75e-03  1.05e+01  9.99e-02  3.68e-03  1.00e+01


   1  7.94e+02  7.05e+01  3.62e+03  7.84e-07  9.73e-01  5.86e-02  1.05e+01  9.44e-02  1.03e-01  1.00e+01


   2  6.39e+02  1.31e+02  2.54e+03  6.85e-07  7.70e-01  1.23e-01  1.05e+01  8.61e-02  2.29e-01  1.00e+01


   3  5.73e+02  1.60e+02  2.07e+03  7.82e-07  3.50e-01  1.41e-01  1.05e+01  8.28e-02  2.04e-01  1.00e+01


...

 195  2.54e+02  9.93e+01  7.73e+02  8.07e-07  3.08e-03  5.18e-03  1.05e+01  1.79e-03  6.47e-03  1.00e+01


 196  2.54e+02  9.93e+01  7.72e+02  8.60e-07  3.07e-03  5.15e-03  1.05e+01  1.78e-03  6.43e-03  1.00e+01


 197  2.54e+02  9.93e+01  7.72e+02  8.37e-07  3.05e-03  5.14e-03  1.05e+01  1.78e-03  6.40e-03  1.00e+01


 198  2.54e+02  9.93e+01  7.72e+02  8.39e-07  3.04e-03  5.12e-03  1.05e+01  1.77e-03  6.37e-03  1.00e+01


 199  2.54e+02  9.92e+01  7.72e+02  7.58e-07  3.02e-03  5.10e-03  1.05e+01  1.76e-03  6.33e-03  1.00e+01
--------------------------------------------------------------------------------------------------------
ConvBPDNDictLearn solve time: 128.97s


Display initial and final dictionaries.

In [7]:
D1 = D1.squeeze()
fig = plot.figure(figsize=(14, 7))
plot.subplot(1, 2, 1)
plot.imview(util.tiledict(D0), title='D0', fig=fig)
plot.subplot(1, 2, 2)
plot.imview(util.tiledict(D1), title='D1', fig=fig)
fig.show()

Get iterations statistics from solver object and plot functional value, ADMM primary and dual residuals, and automatically adjusted ADMM penalty parameter against the iteration number.

In [8]:
its = d.getitstat()
fig = plot.figure(figsize=(20, 5))
plot.subplot(1, 3, 1)
plot.plot(its.ObjFun, xlbl='Iterations', ylbl='Functional', fig=fig)
plot.subplot(1, 3, 2)
plot.plot(np.vstack((its.XPrRsdl, its.XDlRsdl, its.DPrRsdl,
          its.DDlRsdl)).T, ptyp='semilogy', xlbl='Iterations',
          ylbl='Residual', lgnd=['X Primal', 'X Dual', 'D Primal', 'D Dual'],
          fig=fig)
plot.subplot(1, 3, 3)
plot.plot(np.vstack((its.XRho, its.DRho)).T, xlbl='Iterations',
          ylbl='Penalty Parameter', ptyp='semilogy',
          lgnd=['$\\rho_X$', '$\\rho_D$'], fig=fig)
fig.show()